# Прогнозирование выручки от добычи нефти

**Описание проекта**

Вы работаете в добывающей компании «ГлавРосГосНефть». Нужно решить, где бурить новую скважину. 

Шаги для выбора локации обычно такие:
1. В избранном регионе собирают характеристики для скважин: качество нефти и объём её запасов;
2. Строят модель для предсказания объёма запасов в новых скважинах;
3. Выбирают скважины с самыми высокими оценками значений;
4. Определяют регион с максимальной суммарной прибылью отобранных скважин.

Вам предоставлены пробы нефти в трёх регионах. Характеристики для каждой скважины в регионе уже известны. Постройте модель для определения региона, где добыча принесёт наибольшую прибыль. Проанализируйте возможную прибыль и риски техникой `Bootstrap`.

**Описание данных**

Признаки:

1. `id` — уникальный идентификатор скважины;
2. `f0`, `f1`, `f2` — три признака точек (неважно, что они означают, но сами признаки значимы);

Целевой признак:

1. `product` — объём запасов в скважине (тыс. баррелей).

**Дополнительные условия**

1. Для обучения модели подходит только линейная регрессия (остальные — недостаточно предсказуемые).
2. При разведке региона исследуют 500 точек, из которых с помощью машинного обучения выбирают 200 лучших для разработки.
3. Бюджет на разработку скважин в регионе — 10 млрд рублей.
4. При нынешних ценах один баррель сырья приносит 450 рублей дохода. Доход с каждой единицы продукта составляет 450 тыс. рублей, поскольку объём указан в тысячах баррелей.
5. После оценки рисков нужно оставить лишь те регионы, в которых вероятность убытков меньше 2.5%. Среди них выбирают регион с наибольшей средней прибылью.
6. Данные синтетические: детали контрактов и характеристики месторождений не разглашаются.

In [1]:
import pandas as pd
import numpy as np
import plotly.express as px

from plotly.subplots import make_subplots
from IPython.display import display
from collections import defaultdict
from ydata_profiling import ProfileReport

from fast_ml import eda

from sklearn.model_selection import train_test_split

from sklearn.pipeline import Pipeline
from sklearn.preprocessing import StandardScaler

from sklearn.linear_model import LinearRegression

from sklearn.metrics import mean_squared_error

In [2]:
FIG_WIDTH = 10 * 100
FIG_HEIGHT = 5 * 100
RANDOM_SEED = 42
FILE_NAMES = ['geo_data_0', 'geo_data_1', 'geo_data_2']

In [3]:
raw_oil = {}
for file_name in FILE_NAMES:
    try:
        raw_oil[file_name] = pd.read_csv(file_name + '.csv')
    except:
        raw_oil[file_name] = pd.read_csv('/datasets/' + file_name + '.csv')

## Исследовательский анализ данных

Изучим основные зависимости в данных перед тем, как мы будем использовать их в алгоритмах машинного обучения.

Таблица-резюме:

In [4]:
for file_name in FILE_NAMES:
    display(eda.df_info(raw_oil[file_name]))

data_type data_type_grp num_unique_values  \
id         object   Categorical             99990   
f0        float64     Numerical            100000   
f1        float64     Numerical            100000   
f2        float64     Numerical            100000   
product   float64     Numerical            100000   

                                      sample_unique_values num_missing  \
id       [txEyH, 2acmU, 409Wp, iJLyR, Xdl7t, wX4Hy, tL6...           0   
f0       [0.7057449842080644, 1.3347112926051892, 1.022...           0   
f1       [-0.4978225001976334, -0.3401642528583136, 0.1...           0   
f2       [1.22116994843607, 4.3650803324282, 1.41992623...           0   
product  [105.28006184349584, 73.03775026515737, 85.265...           0   

        perc_missing  
id               0.0  
f0               0.0  
f1               0.0  
f2               0.0  
product          0.0

data_type data_type_grp num_unique_values  \
id         object   Categorical             99996   
f0        float64     Numerical            100000   
f1        float64     Numerical            100000   
f2        float64     Numerical            100000   
product   float64     Numerical                12   

                                      sample_unique_values num_missing  \
id       [kBEdx, 62mP7, vyE1P, KcrkZ, AHL4O, HHckp, h5U...           0   
f0       [-15.00134818249185, 14.272087811011149, 6.263...           0   
f1       [-8.275999947188001, -3.47508321506002, -5.948...           0   
f2       [-0.0058760136933206, 0.9991827365665829, 5.00...           0   
product  [3.179102583207246, 26.95326103153969, 134.766...           0   

        perc_missing  
id               0.0  
f0               0.0  
f1               0.0  
f2               0.0  
product          0.0

data_type data_type_grp num_unique_values  \
id         object   Categorical             99996   
f0        float64     Numerical            100000   
f1        float64     Numerical            100000   
f2        float64     Numerical            100000   
product   float64     Numerical            100000   

                                      sample_unique_values num_missing  \
id       [fwXo0, WJtFt, ovLUW, q6cA6, WPMUX, LzZXx, WBH...           0   
f0       [-1.1469870984179529, 0.2627779016539684, 0.19...           0   
f1       [0.9633279217162892, 0.2698389572803021, 0.289...           0   
f2       [-0.8289649221710994, -2.530186515492004, -5.5...           0   
product  [27.75867323073004, 56.06969663239464, 62.8719...           0   

        perc_missing  
id               0.0  
f0               0.0  
f1               0.0  
f2               0.0  
product          0.0

Числовые распределения:

In [5]:
for file_name in FILE_NAMES:
    display(round(raw_oil[file_name].describe().T, 2))

count   mean    std    min    25%    50%     75%     max
f0       100000.0   0.50   0.87  -1.41  -0.07   0.50    1.07    2.36
f1       100000.0   0.25   0.50  -0.85  -0.20   0.25    0.70    1.34
f2       100000.0   2.50   3.25 -12.09   0.29   2.52    4.72   16.00
product  100000.0  92.50  44.29   0.00  56.50  91.85  128.56  185.36

count   mean    std    min    25%    50%     75%     max
f0       100000.0   1.14   8.97 -31.61  -6.30   1.15    8.62   29.42
f1       100000.0  -4.80   5.12 -26.36  -8.27  -4.81   -1.33   18.73
f2       100000.0   2.49   1.70  -0.02   1.00   2.01    4.00    5.02
product  100000.0  68.83  45.94   0.00  26.95  57.09  107.81  137.95

count  mean    std    min    25%    50%     75%     max
f0       100000.0   0.0   1.73  -8.76  -1.16   0.01    1.16    7.24
f1       100000.0  -0.0   1.73  -7.08  -1.17  -0.01    1.16    7.84
f2       100000.0   2.5   3.47 -11.97   0.13   2.48    4.86   16.74
product  100000.0  95.0  44.75   0.00  59.45  94.93  130.60  190.03

И детальный отчет:

In [6]:
for file_name in FILE_NAMES:
    ProfileReport(raw_oil[file_name]).to_widgets()

Render widgets:   0%|          | 0/1 [00:00<?, ?it/s]

Render widgets:   0%|          | 0/1 [00:00<?, ?it/s]

Render widgets:   0%|          | 0/1 [00:00<?, ?it/s]

Ключевые наблюдения из предварительного анализа набора данных:

1. **Качество данных и типы**: Все три набора данных полные и не имеют пропущенных значений в признаках. Это хорошо, поскольку нам не придется заполнять пропуски, и мы можем прямо переходить к анализу и построению модели. Все наборы данных имеют один категориальный признак `id` и четыре числовых признака: `f0`, `f1`, `f2` и `product`. В дальнейшем `id` можно отбросить, потому что с точки зрения модели, нам не нужен уникальный индентификтор скважины.

2. **Уникальные значения**: Количество уникальных значений в `product` удивительно низкое в наборе данных 2: здесь всего 12 уникальных значений по сравнению с 100 000 в двух других наборах данных. Это может указывать на различия в характере данных в наборе данных 2. Возможно, это связано с тем, как данные были собраны.

3. **Распределение данных**: Большинство значений в колонках расперелены нормально, хотя есть несколько выдяляющихся (например, `f0` в первом датасете). Также, в датасете 2 распределение `f2` и `product` сильно отличается от других. Более того, возможно есть какие-то сложные нелинейные зависимости между различными колонками (например, в датасете 1 мы видим два полумесяца для `f0` vs `f1`).

4. **Корреляция**: Корреляция между признаками варьируется в разных наборах данных. В наборе данных 1 заметна отрицательная корреляция между `f0` и `f1`. В наборе данных 2 `f2` показывает очень сильную положительную корреляцию с `product`, что указывает на то, что `f2` может быть значимым предиктором для `product` в этом наборе данных. В наборе данных 3 все корреляции очень слабые, что указывает на менее прямолинейную связь между переменными.

# Обучение ML моделей

Выполним преобразования на этих датасетах - уберем колонки, которые не нужны для моделей: `id`.

И после разделения на выборки, чтобы избежать data leakage - проведем стандартизацию численных признаков.

Наконец, обучим `LogisticRegression` модель для каждого датасета.

In [7]:
dct_oil = defaultdict(dict)
dct_splits = defaultdict(dict)
dct_models = defaultdict(dict)
dct_metrics = defaultdict(dict)

In [8]:
# Define the pipeline
pipeline = Pipeline([
    ('scaler', StandardScaler()),
    ('model', LinearRegression())
])

# Apply transformations
for file_name in FILE_NAMES:
    
    dct_oil[file_name] = raw_oil[file_name].drop('id', axis=1)
    
    ftr_train, ftr_valid, tgt_train, tgt_valid = train_test_split(
        dct_oil[file_name].drop('product', axis=1), dct_oil[file_name]['product'],
        test_size=0.25, random_state=RANDOM_SEED
    )
    
    pipeline.fit(ftr_train, tgt_train)
    
    dct_models[file_name] = pipeline
    
    dct_splits[file_name] = {
        'ftr_train': pd.DataFrame(ftr_train, columns=ftr_train.columns),
        'ftr_valid': pd.DataFrame(ftr_valid, columns=ftr_valid.columns),
        'tgt_train': pd.DataFrame(tgt_train, columns=['product']),
        'tgt_valid': pd.DataFrame(tgt_valid, columns=['product']),
        'tgt_prdct': pd.DataFrame(pipeline.predict(ftr_valid), index=ftr_valid.index, columns=['product'])
    }
    
    dct_metrics[file_name]['rmse'] = mean_squared_error(
        dct_splits[file_name]['tgt_valid'], dct_splits[file_name]['tgt_prdct'],
    ) ** 0.5

Сначала посмотрим на данные.

In [9]:
df_temp = pd.DataFrame()

for file_name in FILE_NAMES:
    df_temp = pd.concat([
        df_temp, 
        dct_splits[file_name]['tgt_prdct'].assign(file_name=file_name, type='prdct'),
        dct_splits[file_name]['tgt_valid'].assign(file_name=file_name, type='valid')
    ])

display(round(df_temp.pivot(columns=['file_name', 'type']).describe(), 1))

fig = px.histogram(
    df_temp,
    x='product',
    color='type',
    facet_col='file_name',
    title='Histogram plots of product from prediction and validation datasets',
    width=FIG_WIDTH,
    height=FIG_HEIGHT,
    template='plotly_white',
)
fig.show()

product                                                 
file_name geo_data_0          geo_data_1          geo_data_2         
type           prdct    valid      prdct    valid      prdct    valid
count        25000.0  25000.0    25000.0  25000.0    25000.0  25000.0
mean            92.4     92.3       68.7     68.7       94.8     95.2
std             23.2     44.3       45.9     45.9       19.9     44.8
min             -9.8      0.0       -2.1      0.0       16.2      0.0
25%             76.8     56.3       28.6     30.1       81.2     59.7
50%             92.4     90.8       57.9     57.1       94.6     94.9
75%            108.0    128.1      109.3    107.8      108.4    130.6
max            176.5    185.4      140.0    137.9      170.5    190.0

А теперь на метрики - сделаем функцию для визуализации.

In [10]:
def create_bar_plot(df, x, y, title, barmode=None):
    """
    This function generates a bar plot using Plotly Express.

    Parameters:
        - df (pandas.DataFrame): DataFrame containing the data to plot.
        - x (str): Column name in df for the x-axis values.
        - y (str): Column name in df for the y-axis values.
        - title (str): Title for the plot.
        - barmode (str, optional): Describes the mode for stacking bars. If 'group', bars are placed beside each other. 
          Default is None, which stacks the bars.

    Returns:
        - None. This function only creates a plot and does not return any values.
    """
    fig = px.bar(
        df, x=x, y=y, 
        title=f"{title} for different datasets",
        width=FIG_WIDTH, height=FIG_HEIGHT,
        template='plotly_white',
        color='variable' if 'variable' in df.columns else None
    )
    if barmode:
        fig.update_layout(barmode=barmode)
    fig.show()

И покажем метрики.

In [11]:
df_temp = pd.DataFrame([
    {
        'file_name': file_name,
        'rmse': dct_metrics[file_name]['rmse'],
        'product_prdct_mean': dct_splits[file_name]['tgt_prdct']['product'].mean(),
        'product_valid_mean': dct_splits[file_name]['tgt_valid']['product'].mean()
    }
    for file_name in FILE_NAMES
]).sort_values(by='rmse')

display(round(df_temp, 2))

create_bar_plot(
    df_temp.sort_values(by='rmse', ascending=False),
    'rmse', 'file_name', 'RMSE of a LinearRegression'
)

create_bar_plot(
    df_temp.drop('rmse', axis=1).melt('file_name'),
    'value', 'file_name', 'Average product', 'group'
)

file_name   rmse  product_prdct_mean  product_valid_mean
1  geo_data_1   0.89               68.71               68.73
0  geo_data_0  37.76               92.40               92.33
2  geo_data_2  40.15               94.77               95.15

Основываясь на RMSE и гистограммах, можно сделать следующие общие выводы:

RMSE: 
   1. RMSE для `geo_data_1` значительно ниже, чем для `geo_data_0` и `geo_data_2`. Это указывает на то, что предсказания модели для `geo_data_1` гораздо ближе к фактическим значениям, по сравнению с другими двумя наборами данных.
   2. RMSE для `geo_data_0` и `geo_data_2` относительно высоки, что свидетельствует о том, что предсказания в общем дальше от фактических значений. Возможно, стоит рассмотреть различные модели или техники инженерии признаков, чтобы уменьшить эти ошибки.

Гистограммы:
   1. Для `geo_data_1` прогнозируемые и фактические значения, более похожи, хотя модель все же плохо предсказывает большие значения (что ожидаемо).
   2. Для `geo_data_0` и `geo_data_2` распределения прогнозируемых и фактических значений повторяют форму распеределения, но модель тоже плохо предсказывает крайние значения.
   3. Для `geo_data_0` и `geo_data_1` у нас закрались несколько отрицательных значений в предсказаниях, что тоже невозможно.

С точки зрения качества модели, эти результаты указывают на то, что наша модель лучше работает на наборе данных `geo_data_1` и может потребовать улучшений для `geo_data_0` и `geo_data_2`. Возможные решения включают: настройку гиперпараметров, использование различных алгоритмов.

# Оценка бизнес-показателей

В последней секции посмотрим на бизнес-метрики: найдем выручку и издержки.

In [12]:
wells_est = 500
wells_dev = 200
budget = 10e9
barrel_price = 450e3
risk_tol = 0.025

Точка безубыточности:

In [13]:
print('Breakeven product volume from a single well:', round(budget / (barrel_price * wells_dev), 2), 'kbarrels')

for file_name in FILE_NAMES:
    print(
        'Average predicted product volume from a single well in',
        file_name, 'region:', round(dct_splits[file_name]['tgt_prdct']['product'].mean(), 2), 'kbarrels'
    )

Breakeven product volume from a single well: 111.11 kbarrels
Average predicted product volume from a single well in geo_data_0 region: 92.4 kbarrels
Average predicted product volume from a single well in geo_data_1 region: 68.71 kbarrels
Average predicted product volume from a single well in geo_data_2 region: 94.77 kbarrels


Наконец, расчет прибыли и риска:

In [14]:
# Create a random number generator with the specified seed
rng = np.random.RandomState(RANDOM_SEED)

results = []

for file_name in FILE_NAMES:
    df = (
        pd.DataFrame({
            'actual_values': dct_splits[file_name]['tgt_valid']['product'],
            'predicted_values': dct_splits[file_name]['tgt_prdct']['product'],
        })
        .assign(
            revenue=lambda df: df.actual_values * barrel_price
        )
    )

    profits = []
    # Perform bootstrapping
    for _ in range(1000):
        profit = (
            df.sample(n=wells_est, random_state=rng)
            .sort_values('predicted_values', ascending=False)
            .iloc[:wells_dev]
            .revenue.sum() - budget
        )
        profits.append(profit)
    
    profits = pd.Series(profits)

    results.append({
        'file_name': file_name,
        'no_wells': wells_dev,
        'mean_profit': profits.mean() / 1e6,
        'lower_bound': profits.quantile(0.025) / 1e6,
        'upper_bound': profits.quantile(0.975) / 1e6,
        'risk': (profits < 0).mean(),
        'profits': profits,
    })

df_results = pd.DataFrame(results)

In [15]:
for idx, row in df_results.iterrows():
    print(
        f"\nFor {row['file_name']} region:"
        f"\nAverage gross profit from 200 best wells selected based on prediction = {row['mean_profit']:.0f} million rubles."
        f"\n95% confidence interval lies between {row['lower_bound']:.0f} - {row['upper_bound']:.0f} million rubles."
        f"\nRisk of loss is {row['risk']:.2%}"
    )
    
    fig = px.histogram(
        row['profits'] / 1e6, nbins=100,
        title=f'Profit distribution for {row["file_name"]}',
        labels={'value': 'Profit, millions'},
        opacity=0.8,
        width=FIG_WIDTH,
        height=FIG_HEIGHT,
        template='plotly_white',
    )
    fig.add_vline(x=row['mean_profit'], line_color="red", line_width=3)
    fig.add_vline(x=row['lower_bound'], line_color="blue", line_width=3)
    fig.add_vline(x=row['upper_bound'], line_color="blue", line_width=3)
    fig.update_layout(showlegend=False)
    fig.update_xaxes(range=[-800, 1500])
    fig.show()


For geo_data_0 region:
Average gross profit from 200 best wells selected based on prediction = 409 million rubles.
95% confidence interval lies between -139 - 952 million rubles.
Risk of loss is 7.40%



For geo_data_1 region:
Average gross profit from 200 best wells selected based on prediction = 436 million rubles.
95% confidence interval lies between 29 - 866 million rubles.
Risk of loss is 1.70%



For geo_data_2 region:
Average gross profit from 200 best wells selected based on prediction = 385 million rubles.
95% confidence interval lies between -186 - 885 million rubles.
Risk of loss is 8.60%


# Выводы

Вот некоторые общие выводы, которые можно сделать из результатов нашей работы:

1. **Среднеквадратическая ошибка (RMSE) моделей линейной регрессии:** Можно заметить, что качество модели значительно отличается в разных регионах. Модель для `geo_data_1` кажется более точной по сравнению с другими двумя, учитывая ее наименьшую RMSE.

2. **Средний прогнозируемый объем продукции от одной скважины:** Все три региона имеют средний прогнозируемый объем, который ниже точки безубыточности на скважину, составляющей 111,11 тыс. баррелей. Поэтому было бы выгодно бурить скважины только в местах с прогнозами выше этой безубыточной точки.

3. **Средняя валовая прибыль от 200 лучших скважин, выбранных на основе прогноза:** Все три региона демонстрируют потенциал для получения прибыли. Однако регион `geo_data_1` предлагает наибольшую среднюю валовую прибыль, несмотря на его более низкий средний прогнозируемый объем продукции на скважину. Это может быть связано с меньшим разбросом в прогнозируемых значениях, что приводит к более высокой точности выбора лучших скважин.

4. **Доверительный интервал:** Доверительные интервалы для всех трех регионов довольно широкие, что указывает на значительную неопределенность в оценках прибыли. Однако у региона `geo_data_1` наименьшая доля его доверительного интервала находится ниже нуля, что указывает на меньший риск в этом регионе.

5. **Риск убытков:** Регион `geo_data_1` имеет наименьший риск убытков, который составляет всего 1,7%. В то время как регионы `geo_data_0` и `geo_data_2` имеют одинаковый риск 7.4% и 8.6% соответственно. Это важный момент, особенно учитывая значительные инвестиции.

В заключение, учитывая как потенциальную прибыль, так и риск убытков, `geo_data_1` кажется наиболее перспективным регионом для разработки.